In [2]:
## This block preprocesses different datasets to vw and csv format
## use 80 % of the original data
import src.datasets.tabular
import src.datasets.utils
from src.datasets.tabular import get_dataset_config


dataset = 'communities-and-crime'
dataset_kwargs = {'root_dir': 'src/datasets'}
filepath = dataset_kwargs['root_dir'] + '/' + dataset
dataset_config = get_dataset_config(dataset, **dataset_kwargs)
dset = src.datasets.utils.get_dataset(dataset_config)
X_tr, y_tr, __, __, __, __ =  dset.get_data()

print(sum(y_tr), len(y_tr))

src.datasets.utils.save_vw_dataset(X_tr, y_tr, dataset, filepath)


src/datasets
1151 1595


In [9]:
dataset_config.sens

['race', 'income_level']

In [1]:
## an example to test whether the eval metric works well in VW dataset
import subprocess, sys, os
VW = 'vw'
ds = 'src/datasets/adult/adult_2.vw.gz'
cmd = [VW, ds, '-b', '24']
# supervised
# cmd += ['--oaa', '2']
# contextual bandit
## --progress 1 means we output all the time loss, otherwise it will only show the time point pow(2,k) 
## param details of different kinds of cb algs are in run_vw_job.py, i.e. the process function.

#cmd += ['--cbify', '2', '--bag', '4', '--progress', '1']
cmd += ['--oaa', '2', '--progress', '1']
output = subprocess.check_output(cmd, stderr=subprocess.STDOUT)

#output = os.system('vw ' + ds + ' -b 24 --oaa 2') 
output = str(output, encoding = 'utf-8')
#output
from src.utils.joint_regret import output_extraction
#the return of output_extraction function is the cummlative loss in terms of the time
loss_all, action_all = output_extraction(output)
#loss_all

# import pandas as pd
# pd.read_csv('')
# group_info = []


['using', 'no', 'cache'] 3
['Reading', 'datafile', '=', 'src/datasets/adult/adult_2.vw.gz'] 4
['num', 'sources', '=', '1'] 4
['Num', 'weight', 'bits', '=', '24'] 5
['learning', 'rate', '=', '0.5'] 4
['initial_t', '=', '0'] 3
['power_t', '=', '0.5'] 3
['Enabled', 'reductions:', 'gd,', 'scorer-identity,', 'oaa'] 5
['Input', 'label', '=', 'MULTICLASS'] 4
['Output', 'pred', '=', 'MULTICLASS'] 4
['average', '', 'since', '', '', '', '', '', '', '', '', 'example', '', '', '', '', '', '', '', 'example', '', '', '', '', '', '', '', 'current', '', '', '', '', '', '', '', 'current', '', 'current'] 38
['loss', '', '', '', '', 'last', '', '', '', '', '', '', '', '', '', 'counter', '', '', '', '', '', '', '', '', 'weight', '', '', '', '', '', '', '', '', '', 'label', '', '', '', '', '', '', '', 'predict', 'features'] 44
['0.000000', '0.000000', '', '', '', '', '', '', '', '', '', '', '', '1', '', '', '', '', '', '', '', '', '', '', '', '1.0', '', '', '', '', '', '', '', '', '', '', '', '', '', '1', 

In [5]:
import pandas as pd
import numpy as np
filepath = 'src/datasets/adult/adult_2.csv'
#df = pd.read_csv('src/datasets/adult/adult_2.csv')
#b = list(np.array(df[['sex', 'race']]))
from src.models.cb.base_cb import base_cb
base_cb_model = base_cb(csvpath = filepath, dataset_class = 'multiclass', 
                        funclass = 'linear', group_name = ['sex', 'race'])
base_cb_model.group
from src.eval_metric_cb import offline_eval_metric_cb
eval_cb_model = offline_eval_metric_cb(group = base_cb_model.group, context = base_cb_model.context_all,
                                        action = action_all, loss = loss_all)

eval_cb_model.group_loss_parity()

/Users/wty6162/Desktop/fa-alg/src/eval_metric_cb.py:46: RuntimeWarning: invalid value encountered in double_scalars
  avg_loss = [cumu_group_loss[i][k] / cumu_group_num[i][k] for k in range(self.group_num)]


{'cumu_loss': 7034.0,
 'cumu_loss_0': 5235.0,
 'cumu_loss_1': 529.0,
 'cumu_loss_2': 166.0,
 'cumu_loss_3': 1104.0,
 'loss_parity': 0.19505509432468415}

In [4]:
!vw src/datasets/adult/adult_2.vw.gz 24 --oaa 2

[warning] Multiple data files passed as positional parameters, only the first one will be read and the rest will be ignored.
using no cache
Reading datafile = src/datasets/adult/adult_2.vw.gz
num sources = 1
Num weight bits = 18
learning rate = 0.5
initial_t = 0
power_t = 0.5
Enabled reductions: gd, scorer-identity, oaa
Input label = MULTICLASS
Output pred = MULTICLASS
average  since         example        example        current        current  current
loss     last          counter         weight          label        predict features
0.000000 0.000000            1            1.0              1              1       11
0.000000 0.000000            2            2.0              1              1       11
0.000000 0.000000            4            4.0              1              1       12
[info] label 2 found -- labels are now considered 1-indexed.
0.000000 0.000000            8            8.0              2              2       11
0.437500 0.875000           16           16.0            

In [1]:
## the falcon procedure, for the paper
## https://arxiv.org/pdf/2003.12699.pdf
from src.models.cb.FALCON import FALCON, FALCON_ldf, FALCON_price
#from split_gz_csv import ds_files_csv, ds_files
#from split import sample_custom_pmf
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import pandas as pd
#from glob_param import *
from src.run_vw_job import process
#from split import *
import re
rgx = re.compile('^average loss = (.*)$', flags=re.M)
#show the regret performance in each algorithm

csv_path = 'src/datasets/adult/adult_2.csv'
# def alg_performance_regret(DS_DIR, did, alg_param, did_type):
loss_param = []
    # if did_type == 'openml':
    #     sample_falcon = FALCON(csv_path, 95, 1)
    # elif did_type == 'ms':
    #     sample_falcon = FALCON_ldf(csv_path, 105, 1, 10)
    # elif did_type == 'yahoo':
    #     sample_falcon = FALCON_ldf(csv_path, 105, 1, 6, 'ridge')
    # elif did_type == 'loan':
    #     if did == 0:
    #         sample_falcon = FALCON_price(csv_path, 10, 1, 15)
    #     elif did == 1:
    #         sample_falcon = FALCON_price(csv_path, 10, 1, 10)
#gamma_param is a hyperparam in FALCON alg.
sample_falcon = FALCON(csvpath = csv_path, gamma_param = 155,
                        group = ['sex', 'race'])
    
sample_falcon.learn_schedule()
#sample_falcon.learn_schedule()

#cummulative loss for FALCON alg.
sample_falcon.loss_all
        

# an example to test whether the eval metric works well in FALCON
from src.eval_metric_cb import offline_eval_metric_cb
eval_falcon = offline_eval_metric_cb(group = sample_falcon.group, context = sample_falcon.context_all,
                              action = sample_falcon.action_all, loss = sample_falcon.loss_all)
eval_falcon.group_loss_parity()
eval_falcon.individual_loss_parity(time_window = 100)
eval_falcon.summary_loss

3
100
200
300
400
500
600
700
800
900
1000
1100
1200
1300
1400
1500
1600
1700
1800
1900
2000
2100
2200
2300
2400
2500
2600
2700
2800
2900
3000
3100
3200
3300
3400
3500
3600
3700
3800
3900
4000
4100
4200
4300
4400
4500
4600
4700
4800
4900
5000
5100
5200
5300
5400
5500
5600
5700
5800
5900
6000
6100
6200
6300
6400
6500
6600
6700
6800
6900
7000
7100
7200
7300
7400
7500
7600
7700
7800
7900
8000
8100
8200
8300
8400
8500
8600
8700
8800
8900
9000
9100
9200
9300
9400
9500
9600
9700
9800
9900
10000
10100
10200
10300
10400
10500
10600
10700
10800
10900
11000
11100
11200
11300
11400
11500
11600
11700
11800
11900
12000
12100
12200
12300
12400
12500
12600
12700
12800
12900
13000
13100
13200
13300
13400
13500
13600
13700
13800
13900
14000
14100
14200
14300
14400
14500
14600
14700
14800
14900
15000
15100
15200
15300
15400
15500
15600
15700
15800
15900
16000
16100
16200
16300
16400
16500
16600
16700
16800
16900
17000
17100
17200
17300
17400
17500
17600
17700
17800
17900
18000
18100
18200
18300
18400
18

{'cumu_loss': 5731.003000000001,
 'avg_loss': 0.1760081999938577,
 'cumu_loss_0': 4217.0,
 'avg_loss_0': 0.21993324293313862,
 'cumu_loss_1': 487.001,
 'avg_loss_1': 0.18616239061070694,
 'cumu_loss_2': 161.001,
 'avg_loss_2': 0.0756227920982658,
 'cumu_loss_3': 866.001,
 'avg_loss_3': 0.10020838923763142,
 'loss_parity': 0.14431045083487282,
 'individual_loss_parity_realized': 11911.0}

In [ ]:
sample_falcon = FALCON(csvpath = csv_path, gamma_param = 155,
                        group = ['sex', 'race'])
    
sample_falcon.learn_schedule(action_fair_type = 'action-parity')
#sample_falcon.learn_schedule()

#cummulative loss for FALCON alg.
sample_falcon.loss_all
        

# an example to test whether the eval metric works well in FALCON
from src.eval_metric_cb import offline_eval_metric_cb
eval_falcon = offline_eval_metric_cb(group = sample_falcon.group, context = sample_falcon.context_all,
                              action = sample_falcon.action_all, loss = sample_falcon.loss_all)
eval_falcon.group_loss_parity()

In [5]:
sample_falcon.learn_schedule()
# an example to test whether the eval metric works well in FALCON
from src.eval_metric_cb import offline_eval_metric_cb
eval_falcon = offline_eval_metric_cb(group = sample_falcon.group, context = sample_falcon.context_all,
                              action = sample_falcon.action_all, loss = sample_falcon.loss_all)
eval_falcon.group_loss_parity()
eval_falcon.group_action_parity()
eval_falcon.summary_loss

3


{'cumu_loss': 5695.003000000001,
 'avg_loss': 0.17490258284450724,
 'cumu_loss_0': 4217.0,
 'avg_loss_0': 0.21993324293313862,
 'cumu_loss_1': 473.001,
 'avg_loss_1': 0.1808107106992696,
 'cumu_loss_2': 161.001,
 'avg_loss_2': 0.0756227920982658,
 'cumu_loss_3': 844.001,
 'avg_loss_3': 0.09766268251993954,
 'loss_parity': 0.14431045083487282,
 'group_action_parity_realized': 0.33976767463976154}

In [3]:
eval_falcon.summary_loss

{'cumu_loss': 7330.003000000001,
 'avg_loss': 0.22511602837750685,
 'cumu_loss_0': 5154.0,
 'avg_loss_0': 0.2688015020340044,
 'cumu_loss_1': 600.001,
 'avg_loss_1': 0.22935809275302263,
 'cumu_loss_2': 269.001,
 'avg_loss_2': 0.12635080960506828,
 'cumu_loss_3': 1307.001,
 'avg_loss_3': 0.1512382375331824,
 'loss_parity': 0.1424506924289361,
 'group_action_parity_realized': 0.33976767463976154}

In [ ]:
output_all = output.split('\n')
res = []
for i in range(len(output_all)):
    if len(output_all[i].split(' ')) >= 50:
        res.append(float(output_all[i].split(' ')[0]))
        #print(len(output_all[i].split(' ')))
    #print(len(output_all[i].split(' ')))
len(res)

In [ ]:
df = pd.read_csv('src/datasets/adult/adult_2.csv')
b = list(np.array(df[['sex', 'race']]))